In [44]:
import pandas as pd
import os
from subprocess import call
from IPython.display import Image
from sklearn.tree import export_graphviz
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.preprocessing import StandardScaler
from dataset_reader import read_dataset

In [45]:
# Load dataset
df = read_dataset()
print(f"Dataset size: {df.shape[0]} rows")
print(f"Columns: {list(df.columns)}")

Dataset size: 20050 rows
Columns: ['_unit_id', '_golden', '_unit_state', '_trusted_judgments', '_last_judgment_at', 'gender', 'gender:confidence', 'profile_yn', 'profile_yn:confidence', 'created', 'description', 'fav_number', 'gender_gold', 'link_color', 'name', 'profile_yn_gold', 'profileimage', 'retweet_count', 'sidebar_color', 'text', 'tweet_coord', 'tweet_count', 'tweet_created', 'tweet_id', 'tweet_location', 'user_timezone']


In [46]:
# Split dataset for test and train sets
dataset_df = df[["fav_number", "tweet_count", "retweet_count", "name", "description", "text", "created"]]

dataset_df = dataset_df.dropna()

dataset_df["name_len"] = dataset_df["name"].str.len()
dataset_df["desc_len"] = dataset_df["description"].str.len()
dataset_df["last_tweet_len"] = dataset_df["text"].str.len()
dataset_df["timestamp"] = pd.to_datetime(dataset_df["created"], format='%m/%d/%Y %M:%S', infer_datetime_format=True).astype(int) / 10**9
dataset_df = dataset_df.drop(["name", "description", "text", "created"], axis=1)

feature_names = ["fav_number", "retweet_count", "name_len", "desc_len", "last_tweet_len", "timestamp"]

train_df, test_df = train_test_split(dataset_df, train_size=0.5)
train_x = train_df.drop("tweet_count", axis=1)
test_x = test_df.drop("tweet_count", axis=1)
train_y = train_df["tweet_count"]
test_y = test_df["tweet_count"]

print(f"Training data rows: {train_df.shape[0]}")
print(f"Test data rows: {test_df.shape[0]}")

Training data rows: 8153
Test data rows: 8153


/tmp/ipykernel_6424/852071713.py:9: FutureWarning: casting datetime64[ns] values to int64 with .astype(...) is deprecated and will raise in a future version. Use .view(...) instead.
  dataset_df["timestamp"] = pd.to_datetime(dataset_df["created"], format='%m/%d/%Y %M:%S', infer_datetime_format=True).astype(int) / 10**9


In [47]:
# Train model
model = RandomForestClassifier(n_estimators=10, max_depth=8)

scaler = StandardScaler()
train_x_scaled = scaler.fit_transform(train_x)
test_x_scaled = scaler.transform(test_x)

model.fit(train_x_scaled, train_y)
prediction = model.predict(test_x_scaled)
test_mse = mean_squared_error(test_y, prediction)
test_mae = mean_absolute_error(test_y, prediction)
print(f"Mean square error: {test_mse}")
print(f"Mean absolute error: {test_mae}")

Mean square error: 1167176410532.187
Mean absolute error: 555806.6443027107


In [48]:
timestamp = int(pd.Timestamp(year=2012, month=9, day=10).timestamp())
_df = pd.DataFrame(data=[{"fav_number": 5000, "retweet_count": 4500, "name_len": 12, "desc_len": 50, "last_tweet_len": 120, "timestamp": timestamp}])

print(_df)
_df_scaled = scaler.transform(_df)
_prediction = model.predict(_df_scaled)
print(_prediction)

   fav_number  retweet_count  name_len  desc_len  last_tweet_len   timestamp
0        5000           4500        12        50             120  1347235200
[21181]


In [49]:
estimator = model.estimators_[5]

tmp_dir = os.path.join(os.getcwd(), 'tmp')
if not os.path.isdir(tmp_dir):
    os.mkdir(tmp_dir)
graph_file = os.path.join(tmp_dir, 'tree.dot')
png_file = os.path.join(tmp_dir, 'tree.png')

export_graphviz(estimator, out_file=graph_file, feature_names=feature_names,
                class_names=None, rounded=True, proportion=False, precision=2, filled=True)

call(['dot', '-Tpng', graph_file, '-o', png_file, '-Gdpi=600'])

Image(filename=png_file)

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.512786 to fit
